In [ ]:
!pip install -U -q transformers datasets accelerate
from huggingface_hub import notebook_login
notebook_login()

In [40]:
from pprint import pprint
from datasets import get_dataset_config_names

def fetch_and_print_configs(dataset_name):
    """helper fn to print configs"""
    configs = get_dataset_config_names(dataset_name)

    print(f"Available configurations for dataset '{dataset_name}':")
    pprint(configs, width=80, compact=True)

    return configs

ds_name = "BEE-spoke-data/govdocs1-by-extension"
configs = fetch_and_print_configs(ds_name)

# Available configurations for dataset 'BEE-spoke-data/knowledge-inoc-concat-v1':
# ['default', 'default-0919', 'smorgasbord', 'tb-interleaved-deduped',
# 'tb-interleaved-deduped-0919', 'tiny-tb-interleaved']

Available configurations for dataset 'BEE-spoke-data/govdocs1-by-extension':
['doc', 'docx', 'logs', 'ppt', 'pptx', 'rtf', 'txt']


In [41]:
from datasets import load_dataset, concatenate_datasets, DatasetDict

def concatenate_and_shuffle_multiple_datasets(datasets_with_configs):
    # Load all datasets with their respective config names
    datasets = [load_dataset(name, config) for name, config in datasets_with_configs]

    # Get all unique splits across the datasets
    all_splits = set(split for ds in datasets for split in ds.keys())

    # Initialize an empty DatasetDict
    combined_dataset = DatasetDict()

    for split in all_splits:
        # Concatenate the same split across all datasets
        datasets_with_split = [ds[split] for ds in datasets if split in ds]
        concatenated = concatenate_datasets(datasets_with_split)

        # Shuffle the concatenated dataset
        shuffled = concatenated.shuffle(seed=80085)

        # Add the shuffled dataset to the combined dataset
        combined_dataset[split] = shuffled

    return combined_dataset


buildlist = [(ds_name, cfg) for cfg in configs]


# Get the combined and shuffled dataset
combined_dataset = concatenate_and_shuffle_multiple_datasets(buildlist)

# Now you can use combined_dataset as needed

Extracting data files:   0%|          | 0/3 [00:00<?, ?it/s]

Generating train split:   0%|          | 0/41393 [00:00<?, ? examples/s]

Generating validation split:   0%|          | 0/1089 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/1090 [00:00<?, ? examples/s]

In [42]:
combined_dataset

DatasetDict({
    test: Dataset({
        features: ['section', 'filename', 'text'],
        num_rows: 4334
    })
    validation: Dataset({
        features: ['section', 'filename', 'text'],
        num_rows: 4328
    })
    train: Dataset({
        features: ['section', 'filename', 'text'],
        num_rows: 159189
    })
})

In [43]:
import re

def word_count(text):
    words = re.findall(r'\b\w+\b', str(text))
    return len(words)

# Example usage
text = "This is a sample text. This text is just an example."
result = word_count(text)
print(result)


11


In [45]:
ds_filtered = combined_dataset.filter(lambda x: word_count(str(x['text'])) > 8,
                                      num_proc=6)
ds_filtered

Filter (num_proc=6):   0%|          | 0/4334 [00:00<?, ? examples/s]

Filter (num_proc=6):   0%|          | 0/4328 [00:00<?, ? examples/s]

Filter (num_proc=6):   0%|          | 0/159189 [00:00<?, ? examples/s]

DatasetDict({
    test: Dataset({
        features: ['section', 'filename', 'text'],
        num_rows: 4334
    })
    validation: Dataset({
        features: ['section', 'filename', 'text'],
        num_rows: 4328
    })
    train: Dataset({
        features: ['section', 'filename', 'text'],
        num_rows: 159185
    })
})

In [ ]:
!pip install langdetect -q
!pip install fasttext-langdetect -q


In [46]:
from ftlangdetect import detect

result = detect(text="Bugün hava çok güzel", low_memory=False)
print(result)

result = detect(text="Bugün hava çok güzel", low_memory=True)
print(result)

result = detect(text="ayy u want sum fuk?", low_memory=True)
print(result)

{'lang': 'tr', 'score': 1.0}
{'lang': 'tr', 'score': 0.9982126951217651}
{'lang': 'en', 'score': 0.9140127301216125}


In [47]:
import re

def normalize_text(text):
    # Remove newlines
    text = text.replace('\n', ' ')

    # Normalize whitespace
    text = re.sub(r'\s+', ' ', text)

    return text

# Example usage
original_text = "This is a\nsample   text with\n\nmultiple   spaces."
normalized_text = normalize_text(original_text)
print(normalized_text)


This is a sample text with multiple spaces.


In [48]:
def get_lang(example):

    return {"lang": detect(text=normalize_text(example['text'])[:6000], low_memory=False)}

ds_filtered = ds_filtered.map(get_lang, num_proc=6)
ds_filtered

Map (num_proc=6):   0%|          | 0/4334 [00:00<?, ? examples/s]

Map (num_proc=6):   0%|          | 0/4328 [00:00<?, ? examples/s]

Map (num_proc=6):   0%|          | 0/159185 [00:00<?, ? examples/s]

DatasetDict({
    test: Dataset({
        features: ['section', 'filename', 'text', 'lang'],
        num_rows: 4334
    })
    validation: Dataset({
        features: ['section', 'filename', 'text', 'lang'],
        num_rows: 4328
    })
    train: Dataset({
        features: ['section', 'filename', 'text', 'lang'],
        num_rows: 159185
    })
})

In [49]:
import pandas as pd

_df = pd.DataFrame(ds_filtered["train"]["lang"], columns=["lang"])
print(_df.lang.value_counts())

en     156342
fr        533
es        520
eu        463
vi        278
ja        172
zh        149
de        141
it        134
ru         95
ceb        90
el         67
pt         42
la         15
oc         15
ko         11
pl         10
th         10
ca          9
sv          8
nl          7
cs          6
sr          6
az          6
no          6
tl          6
ar          5
ro          5
uk          4
tr          3
sk          3
sl          3
id          3
hu          3
ht          2
da          2
fa          2
ms          2
sq          1
ur          1
so          1
bg          1
ml          1
fi          1
lt          1
Name: lang, dtype: int64


In [ ]:
import random
import pprint as pp
pp.pprint(random.choice(ds_filtered['train']['text']))

In [55]:
ds_filtered = ds_filtered.map(lambda x: {'lang': x['lang']['lang']}, num_proc=6)


Map (num_proc=6):   0%|          | 0/4334 [00:00<?, ? examples/s]

Map (num_proc=6):   0%|          | 0/4328 [00:00<?, ? examples/s]

Map (num_proc=6):   0%|          | 0/159185 [00:00<?, ? examples/s]

In [57]:
ds_filtered.push_to_hub(ds_name, "all")

Pushing dataset shards to the dataset hub:   0%|          | 0/1 [00:00<?, ?it/s]

Creating parquet from Arrow format:   0%|          | 0/5 [00:00<?, ?ba/s]

Deleting unused files from dataset repository:   0%|          | 0/1 [00:00<?, ?it/s]

Pushing dataset shards to the dataset hub:   0%|          | 0/1 [00:00<?, ?it/s]

Creating parquet from Arrow format:   0%|          | 0/5 [00:00<?, ?ba/s]

...

Creating parquet from Arrow format:   0%|          | 0/11 [00:00<?, ?ba/s]

Creating parquet from Arrow format:   0%|          | 0/11 [00:00<?, ?ba/s]

Creating parquet from Arrow format:   0%|          | 0/11 [00:00<?, ?ba/s]

Creating parquet from Arrow format:   0%|          | 0/11 [00:00<?, ?ba/s]

Deleting unused files from dataset repository:   0%|          | 0/15 [00:00<?, ?it/s]

# New Section

In [52]:
!pip install textstat -q
import textstat

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 105.1/105.1 kB 2.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.0/2.0 MB 29.5 MB/s eta 0:00:00


In [56]:
ds_filtered['train'][0]

{'section': 'converted_docs',
 'filename': '356139',
 'text': "**DiamondMEMS\\***\n\nJohn A. Carlisle\n\nMaterials Science Division & Center for Nanoscale Materials\n\nArgonne National Laboratory\n\nArgonne, Illinois 60439 USA\n\nDiamond MEMS may offer many potential performance and reliability\nadvantages over traditional MEMS materials. For instance, its high\nYoung's modulus may enable diamond RF MEMS devices to operate at\nunprecedented high frequencies, whereas the surface chemistry of\ndiamond, which gives rise to it's low friction and stiction properties,\nmay greatly enhance the reliability of these devices, simplify the\ncomplexity of their design and also possibility greatly reduce packaging\ncosts (e.g. the need for anti-stiction coatings and hermetic packaging).\nHowever, there are many challenges to be overcome if the dream is to\nbecome a reality. Like any other thin film technology, diamond films\nmust integrate with many other different materials (semiconductors,\nmetal

In [58]:
ds_f2 = ds_filtered.filter(lambda x: x['lang']== 'en', num_proc=6)
ds_f2

Filter (num_proc=6):   0%|          | 0/4334 [00:00<?, ? examples/s]

Filter (num_proc=6):   0%|          | 0/4328 [00:00<?, ? examples/s]

Filter (num_proc=6):   0%|          | 0/159185 [00:00<?, ? examples/s]

DatasetDict({
    test: Dataset({
        features: ['section', 'filename', 'text', 'lang'],
        num_rows: 4258
    })
    validation: Dataset({
        features: ['section', 'filename', 'text', 'lang'],
        num_rows: 4263
    })
    train: Dataset({
        features: ['section', 'filename', 'text', 'lang'],
        num_rows: 156342
    })
})

In [59]:
import textstat

def get_ease(example):

    return {"flesch_reading_ease": textstat.flesch_reading_ease(example['text'])}

ds_f2  = ds_f2.map(get_ease, num_proc=7)

import pandas as pd

_df = pd.DataFrame(ds_f2["train"]["flesch_reading_ease"], columns=["flesch_reading_ease"])
print(_df.describe())

Map (num_proc=7):   0%|          | 0/4258 [00:00<?, ? examples/s]

Map (num_proc=7):   0%|          | 0/4263 [00:00<?, ? examples/s]

Map (num_proc=7):   0%|          | 0/156342 [00:00<?, ? examples/s]

       flesch_reading_ease
count        156342.000000
mean             24.976902
std             716.462062
min         -220621.670000
25%              28.910000
50%              43.430000
75%              55.470000
max             120.210000


In [62]:
ds_f2 = ds_f2.filter(lambda x: x['flesch_reading_ease'] > 20)
ds_f2

Filter:   0%|          | 0/4258 [00:00<?, ? examples/s]

Filter:   0%|          | 0/4263 [00:00<?, ? examples/s]

Filter:   0%|          | 0/156342 [00:00<?, ? examples/s]

DatasetDict({
    test: Dataset({
        features: ['section', 'filename', 'text', 'lang', 'flesch_reading_ease'],
        num_rows: 3549
    })
    validation: Dataset({
        features: ['section', 'filename', 'text', 'lang', 'flesch_reading_ease'],
        num_rows: 3541
    })
    train: Dataset({
        features: ['section', 'filename', 'text', 'lang', 'flesch_reading_ease'],
        num_rows: 129653
    })
})

In [64]:
ds_f2 = ds_f2.remove_columns(['lang',])
ds_f2

DatasetDict({
    test: Dataset({
        features: ['filename', 'text', 'flesch_reading_ease'],
        num_rows: 3549
    })
    validation: Dataset({
        features: ['filename', 'text', 'flesch_reading_ease'],
        num_rows: 3541
    })
    train: Dataset({
        features: ['filename', 'text', 'flesch_reading_ease'],
        num_rows: 129653
    })
})

In [66]:
ds_f2.push_to_hub(ds_name, "all-filtered")

Pushing dataset shards to the dataset hub:   0%|          | 0/1 [00:00<?, ?it/s]

Creating parquet from Arrow format:   0%|          | 0/4 [00:00<?, ?ba/s]

Deleting unused files from dataset repository:   0%|          | 0/1 [00:00<?, ?it/s]

Pushing dataset shards to the dataset hub:   0%|          | 0/1 [00:00<?, ?it/s]

Creating parquet from Arrow format:   0%|          | 0/4 [00:00<?, ?ba/s]

...

Creating parquet from Arrow format:   0%|          | 0/10 [00:00<?, ?ba/s]

Creating parquet from Arrow format:   0%|          | 0/10 [00:00<?, ?ba/s]

Creating parquet from Arrow format:   0%|          | 0/10 [00:00<?, ?ba/s]

Creating parquet from Arrow format:   0%|          | 0/10 [00:00<?, ?ba/s]

Deleting unused files from dataset repository:   0%|          | 0/2 [00:00<?, ?it/s]